# Goal

<h3 style="color:blue">assess the quality of summaries written by students</h3>
<h3 style="color:indigo">evaluate how well a student represents the main idea and details of a source text, as well as the clarity, precision, and fluency of the language used in the summary</h3>
<h3 style="color:red">Freely & publicly available external data is <b>allowed</b>, including pre-trained models</h3>
<h3>This is Multi-Output problem</h3>

### Use Hugging Face Library
### Use NLTK
### Use Tensorflow

In [1]:
import warnings
warnings.filterwarnings("ignore")

In [2]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

import re
import math
import subprocess
from tqdm import tqdm


In [28]:
import tensorflow as tf

In [29]:
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, r2_score, mean_absolute_error, explained_variance_score, median_absolute_error

In [5]:
import transformers
from transformers import AutoTokenizer, TFBertModel

In [6]:
pip install -U sentence-transformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 kB 3.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for sentence-transformers: filename=sentence_transformers-2.2.2-py3-none-any.whl size=125938 sha256=82dd5b4fe039c8f87e7a0015802d756636d4d87c3b78525277c24cc9bf821613
  Stored in directory: /root/.cache/pip/wheels/62/f2/10/1e606fd5f02395388f74e7462910fe851042f97238cbbd902f
Successfully built sentence-transformers
Note: you may need to restart the kernel to use updated packages.


In [7]:
prompts_train = pd.read_csv('/kaggle/input/commonlit-evaluate-student-summaries/prompts_train.csv')
summaries_train = pd.read_csv('/kaggle/input/commonlit-evaluate-student-summaries/summaries_train.csv')
prompts_test = pd.read_csv('/kaggle/input/commonlit-evaluate-student-summaries/prompts_test.csv')
summaries_test = pd.read_csv('/kaggle/input/commonlit-evaluate-student-summaries/summaries_test.csv')

In [8]:
train = pd.merge(prompts_train, summaries_train, on='prompt_id')
test = pd.merge(prompts_test, summaries_test, on='prompt_id')

In [9]:
train.rename(columns = {'text' : 'summary'}, inplace=True)
test.rename(columns = {'text' : 'summary'}, inplace=True)

In [10]:
train.head(2)

prompt_id                                    prompt_question prompt_title  \
0    39c16e  Summarize at least 3 elements of an ideal trag...   On Tragedy   
1    39c16e  Summarize at least 3 elements of an ideal trag...   On Tragedy   

                                         prompt_text    student_id  \
0  Chapter 13 \r\nAs the sequel to what has alrea...  00791789cc1f   
1  Chapter 13 \r\nAs the sequel to what has alrea...  0086ef22de8f   

                                             summary   content   wording  
0  1 element of an ideal tragedy is that it shoul... -0.210614 -0.471415  
1  The three elements of an ideal tragedy are:  H... -0.970237 -0.417058

In [11]:
train['summary'][0]

'1 element of an ideal tragedy is that it should be arranged on a complex plan.  Another element of an ideal tragedy is that it should only have one main issue. The last element of an ideal tragedy is that it should have a double thread plot and an opposite catastrophe for both good and bad.'

In [12]:
columns_needed = ["prompt_text", "summary"]

### Do Sentence Tokenization
### https://huggingface.co/sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2

In [13]:
from sentence_transformers import SentenceTransformer

In [14]:
train_data = train[columns_needed]

In [15]:
train_data

prompt_text  \
0     Chapter 13 \r\nAs the sequel to what has alrea...   
1     Chapter 13 \r\nAs the sequel to what has alrea...   
2     Chapter 13 \r\nAs the sequel to what has alrea...   
3     Chapter 13 \r\nAs the sequel to what has alrea...   
4     Chapter 13 \r\nAs the sequel to what has alrea...   
...                                                 ...   
7160  With one member trimming beef in a cannery, an...   
7161  With one member trimming beef in a cannery, an...   
7162  With one member trimming beef in a cannery, an...   
7163  With one member trimming beef in a cannery, an...   
7164  With one member trimming beef in a cannery, an...   

                                                summary  
0     1 element of an ideal tragedy is that it shoul...  
1     The three elements of an ideal tragedy are:  H...  
2     Aristotle states that an ideal tragedy should ...  
3     One element of an Ideal tragedy is having a co...  
4     The 3 ideal of tragedy is how complex you need...  
...                                                 ...  
7160  In paragraph two, they would use pickle meat a...  
7161  in the first paragraph  it says "either can it...  
7162  They would have piles of filthy meat on the fl...  
7163  They used all sorts of chemical concoctions to...  
7164  The meat would smell sour but the would "rub i...  

[7165 rows x 2 columns]

In [16]:
model = SentenceTransformer('sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2')

In [18]:
def vectorization(column, train_data, model):
    new_column = []

    for row_index, row in enumerate(tqdm(train_data[column])):
        data = row
        lisst = []

        for d in data.split("."):
            lisst.append(d)

        embeddings = model.encode(lisst)

        mean_embedding = np.mean(embeddings)
        new_column.append(mean_embedding)

    return new_column

In [ ]:
for column in columns_needed:
    train_data[column + '_embeddings'] = vectorization(column, train_data, model)

  0%|          | 0/7165 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 1/7165 [00:00<1:32:10,  1.30it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 2/7165 [00:01<1:30:16,  1.32it/s]

...

 98%|█████████▊| 7023/7165 [16:09<00:20,  6.84it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

 98%|█████████▊| 7025/7165 [16:09<00:20,  6.87it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

In [22]:
train_sentence_embeddings = train_data[['prompt_text_embeddings', 'summary_embeddings']]

In [24]:
train_sentence_embeddings.to_csv('train_sentence_embeddings.csv', index=False)

In [25]:
import pickle
with open("train_sentence_embeddings.pkl", "wb") as file:
    pickle.dump(train_sentence_embeddings, file)

In [31]:
import xgboost as xgb

In [35]:
X_train, X_test, y_train, y_test = train_test_split(train_sentence_embeddings, train['content'], test_size=0.2, random_state=42)


In [32]:
xgbooster = xgb.XGBRegressor()

In [36]:
xgbooster.fit(X_train, y_train)

XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             gamma=None, gpu_id=None, grow_policy=None, importance_type=None,
             interaction_constraints=None, learning_rate=None, max_bin=None,
             max_cat_threshold=None, max_cat_to_onehot=None,
             max_delta_step=None, max_depth=None, max_leaves=None,
             min_child_weight=None, missing=nan, monotone_constraints=None,
             n_estimators=100, n_jobs=None, num_parallel_tree=None,
             predictor=None, random_state=None, ...)

In [40]:
prediction = xgbooster.predict(X_test)

In [41]:
y_test

1706   -0.431734
457     3.005642
6508    0.205683
5690    1.284505
6844    1.819545
          ...   
2651   -0.093814
4955    0.205683
279    -0.040890
2764    0.297031
2476    0.205683
Name: content, Length: 1433, dtype: float64

In [43]:
mse = mean_squared_error(y_test, prediction)

In [44]:
mse

0.9099793962475219